
## Calculate keyword similarity score (evaluation) <br>

In the following, we use the overlap coefficient to compute the keyword similarity score of the keywords extracted from the evaluation data:

In [2]:
import os
from bs4 import BeautifulSoup
import json
import pandas as pd
import numpy as np
import math
from googletrans import Translator # pip install googletrans==4.0.0-rc1
translator = Translator()

In [7]:
eval_df = pd.read_csv ('eval/_EVAL_details_in_df.csv')

eval_df

pair_id url1_lang url2_lang  \
0     1484189203_1484121193        en        en   
1     1484011097_1484011106        en        en   
2     1484039488_1484261803        en        en   
3     1484332324_1484796748        en        en   
4     1484012256_1484419682        en        en   
...                     ...       ...       ...   
4897  1553907621_1553488848        es        it   
4898  1646957948_1643667075        es        it   
4899  1504063453_1502866628        es        it   
4900  1647862428_1647712939        es        it   
4901  1636570015_1637492652        es        it   

                                                 title1  \
0        Police: 2 men stole tools from Lowe’s in Davie   
1     Open database leaked 179GB in customer, US gov...   
2     Ducks are own worst enemies in sloppy loss in ...   
3     Another Bengal vs Centre tussle? Govt rejects ...   
4     Bars and clubs you loved and lost this decade ...   
...                                                 ...   
4897  Denver Nuggets reporta que “un miembro de la o...   
4898  Vivir en España es más barato que en la media ...   
4899  Activan sistema de vigilancia epidemiológica e...   
4900  Emite Irán orden de arresto contra Tump por as...   
4901  Biden, con más de 10 puntos que Trump en estad...   

                                                 title2  \
0      No-swim advisory lifted for Deerfield Beach Pier   
1     Best Western’s Massive Data Leak: 179GB Amazon...   
2     Woody Guthrie's 1943 New Year's Resolutions ar...   
3     'Congress Rejected 7 Times': BJP's Reminder as...   
4                             Top 20 films of the 2010s   
...                                                 ...   
4897    Coronavirus, un caso anche fra i Denver Nuggets   
4898  Coronavirus, in Europa 140mila morti in più in...   
4899  Coronavirus in Cina: consumo di serpenti e zup...   
4900  Iran emette mandato di arresto per Trump per l...   
4901  Sondaggio Usa 2020: Biden in vantaggio nei 6 S...   

                                              keywords1  \
0                        More Trending Stories,Trending   
1     AI,Hardware,Executive Guides,Cloud,Microsoft,S...   
2                                         anaheim-ducks   
3     bengal latest news,mamata banrjee,republicday,...   
4     Broad Street Birmingham,ThingsToDoInBirmingham...   
...                                                 ...   
4897                                         Denver,NBA   
4898                                           EUROSTAT   
4899           vigilancia epidemiológica,ticker,puertos   
4900  ESTADOS UNIDOS,ESTADOSUNIDOS,DONALDTRUMP,IRÁN,...   
4901                                                NaN   

                                              keywords2  \
0                        More Trending Stories,Trending   
1     Best Western,Information Security,Privacy,aws,...   
2     keep the hope machine running,new year's resol...   
3     tableaux,WestBengal,Mamata Banerjee,West Benga...   
4     Marvel Cinematic Universe,People's Struggles,a...   
...                                                 ...   
4897  DenverNuggets,coronavirus,Denver Nuggets,Coron...   
4898                                             Estero   
4899                                           serpenti   
4900  corpodelleguardie,magistratura,iran,qasemsolei...   
4901                       JoeBiden,DonaldTrump,NewYork   

                                                  text1  \
0     DAVIE, FLA. (WSVN) - Police need help catching...   
1     Govt officials confirm Trump can block US comp...   
2     Ducks defenseman Erik Gudbranson, left, knocks...   
3     The West Bengal government’s proposal was reje...   
4     The video will start in 8 Cancel\n\nSign up to...   
...                                                 ...   
4897  Los Denver Nuggets de la NBA reportaron este j...   
4898  El estudio realizado por Eurostat muestra que ...   
4899  Foto: Archivo Foto: Archivo\n\nEl 

In [3]:
keywords_score_df = pd.DataFrame(columns = ["pair_id","url1_lang", "url2_lang", "key1","key2","key1_translated","key2_translated"])



### Overlap coefficient for keywords <br>

We treat keywords in a similar fashion as the named entities (see `13_get_evaluation_title_named_entity_similarity_score.ipynb`) and we use the overlap coefficient to measure similarity. Whenever keywords are not available, the score is set to -1.0.<br><br>

Analogously to the case of named entities, we translate and normalize keywords to English before comparing them. This requires to take extra care because of the limitations of the Google Translate API. In particular, we have to manually set a threshold to prevent being banned by Google Translate.<br><br>

We start by comparing the pairs that do not require translation and, afterwards, we deal with the ones that require translation.

In [4]:
def normalize(input_list):
     return [(((e.lower()).replace('.','')).replace('-',' ')).replace("'s", "") for e in input_list]


def overlapScore(key1, key2):
    key1 = set(key1)
    key2 = set(key2)
    interset = key1.intersection(key2)
    union = key1.union(key2)
    
    denominator = len(key1)
    if len(key2) < denominator:
        denominator = len(key2)
    
    if len(key1) <1 or len(key2) <1 or len(union) < 1 or len(interset)<1:
        return 0
    return (len(interset)/(denominator))


# first do the ones that don't need translation (same lang can directly map to to each other)
# only when its different language paired together do we need to translate them to english then compare
for i, row in eval_df.iterrows():
    pair = row['pair_id']
    score = -1
    key1 = ''
    key2 = ''
    key1_translated = ''
    key2_translated = ''
    print('--------------',i,'---------------')
    print(pair)
    if isinstance(row['keywords1'], str) and isinstance(row['keywords2'], str):
        score = 0
        key1 = row['keywords1'].split(",")
        key2 = row['keywords2'].split(",")

        key1_translated = row['keywords1']
        key2_translated = row['keywords2']
        score = overlapScore(key1, key2)
    
        if row['url1_lang'] != row['url2_lang']:
            trans.append(i)
    entry = {'pair_id':pair,'url1_lang':row['url1_lang'],'url2_lang':row['url2_lang'],'key1':row['keywords1'],'key2':row['keywords2'],'key1_translated':key1_translated,'key2_translated':key2_translated,'score':score}
    print('entry:\n',entry)
    keywords_score_df = keywords_score_df.append(entry, ignore_index = True)



-------------- 0 ---------------
1484189203_1484121193
entry:
 {'pair_id': '1484189203_1484121193', 'url1_lang': 'en', 'url2_lang': 'en', 'key1': 'More Trending Stories,Trending', 'key2': 'More Trending Stories,Trending', 'key1_translated': 'More Trending Stories,Trending', 'key2_translated': 'More Trending Stories,Trending', 'score': 1.0}


C:\Users\Potsdam\AppData\Local\Temp\ipykernel_18728\2528427711.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  keywords_score_df = keywords_score_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_18728\2528427711.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  keywords_score_df = keywords_score_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_18728\2528427711.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  keywords_score_df = keywords_score_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_18728\2528427711.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future

-------------- 1 ---------------
1484011097_1484011106
entry:
 {'pair_id': '1484011097_1484011106', 'url1_lang': 'en', 'url2_lang': 'en', 'key1': 'AI,Hardware,Executive Guides,Cloud,Microsoft,Security TV,Topics,See All Topics,Innovation,5G,Government - US,CXO,Data Management,Data Centers,Apple,Security,Windows 10', 'key2': 'Best Western,Information Security,Privacy,aws,Cybersecurity,Autoclerk,Data breach,SecurityNews,SB Blogwatch,security,Security News,Data Security', 'key1_translated': 'AI,Hardware,Executive Guides,Cloud,Microsoft,Security TV,Topics,See All Topics,Innovation,5G,Government - US,CXO,Data Management,Data Centers,Apple,Security,Windows 10', 'key2_translated': 'Best Western,Information Security,Privacy,aws,Cybersecurity,Autoclerk,Data breach,SecurityNews,SB Blogwatch,security,Security News,Data Security', 'score': 0.03571428571428571}
-------------- 2 ---------------
1484039488_1484261803
entry:
 {'pair_id': '1484039488_1484261803', 'url1_lang': 'en', 'url2_lang': 'en', 'k

C:\Users\Potsdam\AppData\Local\Temp\ipykernel_18728\2528427711.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  keywords_score_df = keywords_score_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_18728\2528427711.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  keywords_score_df = keywords_score_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_18728\2528427711.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  keywords_score_df = keywords_score_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_18728\2528427711.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future

-------------- 14 ---------------
1484188945_1484188562
entry:
 {'pair_id': '1484188945_1484188562', 'url1_lang': 'en', 'url2_lang': 'en', 'key1': 'Sean MacGillis,TSE:6758,Daniel Mitre,Tencent,NASDAQ:MSFT,Activision Blizzard,CSE:EPY,Microsoft,ePlay Digital,The Nielsen Company,US,China,NYSE:NLSN,NYSE:SNE,Erik Dekker,HKEX:0700,NASDAQ:ATVI,Sony,Trevor Doerksen,Nick Mersch', 'key2': 'UKNews,UK News,tendendo', 'key1_translated': 'Sean MacGillis,TSE:6758,Daniel Mitre,Tencent,NASDAQ:MSFT,Activision Blizzard,CSE:EPY,Microsoft,ePlay Digital,The Nielsen Company,US,China,NYSE:NLSN,NYSE:SNE,Erik Dekker,HKEX:0700,NASDAQ:ATVI,Sony,Trevor Doerksen,Nick Mersch', 'key2_translated': 'UKNews,UK News,tendendo', 'score': 0}
-------------- 15 ---------------
1484452733_1484215051
entry:
 {'pair_id': '1484452733_1484215051', 'url1_lang': 'en', 'url2_lang': 'en', 'key1': 'Dirty Dining,Golf,Dolphins,News,Cuba,Holidays,Florida State Seminoles,Broward County,Concerts,Local,Local 10 Digi Shorts,BrowardCounty,Miam

...

C:\Users\Potsdam\AppData\Local\Temp\ipykernel_18728\2528427711.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  keywords_score_df = keywords_score_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_18728\2528427711.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  keywords_score_df = keywords_score_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_18728\2528427711.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  keywords_score_df = keywords_score_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_18728\2528427711.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future

-------------- 4873 ---------------
1605019930_1606873908
entry:
 {'pair_id': '1605019930_1606873908', 'url1_lang': 'zh', 'url2_lang': 'zh', 'key1': '魏凤和', 'key2': '魏凤和', 'key1_translated': '魏凤和', 'key2_translated': '魏凤和', 'score': 1.0}
-------------- 4874 ---------------
1629652077_1629485929
entry:
 {'pair_id': '1629652077_1629485929', 'url1_lang': 'zh', 'url2_lang': 'zh', 'key1': nan, 'key2': '习近平 总书记 志愿者代表 社区志愿者 志愿者服务队 社会主义 志愿服务 2005年 回族,习近平总书记志愿者代表社区志愿者志愿者服务队社会主义志愿服务2005年回族', 'key1_translated': '', 'key2_translated': '', 'score': -1}
-------------- 4875 ---------------
1576847578_1576936547
entry:
 {'pair_id': '1576847578_1576936547', 'url1_lang': 'zh', 'url2_lang': 'zh', 'key1': '不戴口罩将被列入北京游园不文明行为“黑名单”', 'key2': '江苏援武汉最后一支医疗队“回家” 与战友拥抱泪别,江苏援武汉最后一支医疗队“回家”与战友拥抱泪别', 'key1_translated': '不戴口罩将被列入北京游园不文明行为“黑名单”', 'key2_translated': '江苏援武汉最后一支医疗队“回家” 与战友拥抱泪别,江苏援武汉最后一支医疗队“回家”与战友拥抱泪别', 'score': 0}
-------------- 4876 ---------------
1506442713_1503323632
entry:
 {'pair_id': '1506442713_15

C:\Users\Potsdam\AppData\Local\Temp\ipykernel_18728\2528427711.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  keywords_score_df = keywords_score_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_18728\2528427711.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  keywords_score_df = keywords_score_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_18728\2528427711.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  keywords_score_df = keywords_score_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_18728\2528427711.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future

-------------- 4884 ---------------
1535998678_1539210601
entry:
 {'pair_id': '1535998678_1539210601', 'url1_lang': 'de', 'url2_lang': 'en', 'key1': 'Putin,Eskalation,März,5,Erdogan,Idlib,Moskau', 'key2': nan, 'key1_translated': '', 'key2_translated': '', 'score': -1}
-------------- 4885 ---------------
1536278830_1536316493
entry:
 {'pair_id': '1536278830_1536316493', 'url1_lang': 'de', 'url2_lang': 'en', 'key1': 'Musik,Flavor Flav,STD,Rauswurf,3,INT,Rapper,Medien,Public Enemy,PublicEnemy,Hören,ChuckD,FlavorFlav,Chuck D,ART', 'key2': 'Flavor Flav,Public Enemy,cease and desist,PublicEnemy,bernie sanders', 'key1_translated': 'Musik,Flavor Flav,STD,Rauswurf,3,INT,Rapper,Medien,Public Enemy,PublicEnemy,Hören,ChuckD,FlavorFlav,Chuck D,ART', 'key2_translated': 'Flavor Flav,Public Enemy,cease and desist,PublicEnemy,bernie sanders', 'score': 0.17647058823529413}
-------------- 4886 ---------------
1561993331_1560563711
entry:
 {'pair_id': '1561993331_1560563711', 'url1_lang': 'de', 'url2_lang

C:\Users\Potsdam\AppData\Local\Temp\ipykernel_18728\2528427711.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  keywords_score_df = keywords_score_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_18728\2528427711.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  keywords_score_df = keywords_score_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_18728\2528427711.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  keywords_score_df = keywords_score_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_18728\2528427711.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future

In [51]:
# threshold needed because translating keywords using googletran sometimes produce a timeout that we have to restart 
# to continue translating for later keywords
threshold = 4041

for i, row in eval_df.iterrows():
    pair = row['pair_id']
    score = -1
    key1 = ''
    key2 = ''
    key1_translated = ''
    key2_translated = ''
    
    if isinstance(row['keywords1'], str) and isinstance(row['keywords2'], str):
        score = 0
        key1 = row['keywords1'].split(",")
        key2 = row['keywords2'].split(",")

        if row['url1_lang'] != row['url2_lang'] and i >= threshold:
         
            print('--------------',i,'---------------')
            print(pair)
            key1_translated = []
            key2_translated = []
            
            print(row['url1_lang'],' ',row['url2_lang'])
            print('og 1:',row['keywords1'])
            print('og 2:',row['keywords2'])

            for k in key1:
#                 print(k)
                if k == 'alertadigital.com' or k == 'fakty.interia.pl' or k[-3:]=='.lu'  or k[-3:]=='.it' or k[-3:]=='.pl' or len(k)<1 or not isinstance(k,str):
                    continue
                
                if row['url1_lang'] == 'zh':
                    result = translator.translate(k,src='zh-cn')
                else:
                    result = translator.translate(k,src=row['url1_lang'])
                key1_translated.append(result.text)

            for k in key2:
#                 print(row['url2_lang'])
#                 print(k)
                if k == 'www.ynet.co.il' or k[-3:]=='.pl' or k[-3:]=='.lu' or k[-3:]=='.it' or len(k)<1 or not isinstance(k,str):
                    continue
                if row['url2_lang'] == 'zh':
                    result = translator.translate(k,src='zh-cn')
                else:
                    result = translator.translate(k,src=row['url2_lang'])
                key2_translated.append(result.text)

            print('trans 1:',key1_translated)
            print('trans 2:',key2_translated)
            
            if row['url1_lang'] == 'en' or row['url2_lang'] == 'en':
                score = overlapScore(normalize(key1),normalize(key2)
                
            score_trans = overlapScore(normalize(key1_translated),normalize(key2_translated))
            print('score:',score)
            # because sometimes translation could mess up the keywords (eg. Adam Schiff a person's name can be 'mistranslated' to 'adam ship')
            # we want to only store the score that's higher 
            print('score_trans:',score_trans)
            if score_trans > score:
                score = score_trans
            print('final score:',score)
            
            
            key1_translated = ','.join(key1_translated)
            key2_translated = ','.join(key2_translated)
            print('key1trans:',key1_translated)

            keywords_score_df.at[i,'key1_translated'] = key1_translated
            keywords_score_df.at[i,'key2_translated'] = key2_translated
            keywords_score_df.at[i,'score'] = score
            print('iloc:',keywords_score_df.iloc[i]['key1_translated'])



-------------- 4041 ---------------
1568735370_1571102568
fr   pl
og 1: Régions,Argent,Bourse,étranger,Journal,lessentiel.lu,Marchés,Dossier,rechercher,gratuit,etranger,Sport,régional,international,depeches,Nouvelles,GrandeRégion,News,Economie,Luxembourg,Dépêches,Medias,L'essentiel,meteo,regional,regions,Grande Région,Newsvonjetzt,www.lessentiel.lu,News von jetzt,Météo,nouveau
og 2: fakty.interia.pl,świat,faktydnia
trans 1: ['Regions', 'Money', 'stock Exchange', 'foreigner', 'Newspaper', 'Markets', 'Case', 'to research', 'free', 'foreigner', 'Sport', 'regional', 'international', 'deletions', 'News', 'Grandegion', 'News', 'Economy', 'Luxembourg', 'Dispatch', 'Media', 'The essential', 'weather report', 'regional', 'regions', 'Great region', 'News von Jetzt', 'News von Jetzt', 'Weather report', 'new']
trans 2: ['world', 'factual']
score: 0
score_trans: 0
final score: 0
key1trans: Regions,Money,stock Exchange,foreigner,Newspaper,Markets,Case,to research,free,foreigner,Sport,regional,intern

trans 1: ['Weinstein.', 'CulpableDeddownSexplaysExitoryHistoricalParameToo :: Journal', 'guilty of two sexual crimes in historical trial for methoo :: periodic the exposure of Puerto Rico :: USA Hispanics']
trans 2: ['Prescription', 'Pd', 'harassment', 'Weinstein', 'Weinstein Process', 'UBI Banca', 'Weinstein Harvey', 'Weinstein Harvey', 'Weinstein Process', 'Coronavirus', 'Weinstein accusations', 'Weinstein accusations']
score: 0
score_trans: 0.09090909090909091
final score: 0.09090909090909091
key1trans: Weinstein.,CulpableDeddownSexplaysExitoryHistoricalParameToo :: Journal,guilty of two sexual crimes in historical trial for methoo :: periodic the exposure of Puerto Rico :: USA Hispanics
iloc: Weinstein.,CulpableDeddownSexplaysExitoryHistoricalParameToo :: Journal,guilty of two sexual crimes in historical trial for methoo :: periodic the exposure of Puerto Rico :: USA Hispanics
-------------- 4897 ---------------
1553907621_1553488848
es   it
og 1: Denver,NBA
og 2: DenverNuggets,cor

In [24]:
keywords_score_df

pair_id url1_lang url2_lang  \
0     1484189203_1484121193        en        en   
1     1484011097_1484011106        en        en   
2     1484039488_1484261803        en        en   
3     1484332324_1484796748        en        en   
4     1484012256_1484419682        en        en   
...                     ...       ...       ...   
4897  1553907621_1553488848        es        it   
4898  1646957948_1643667075        es        it   
4899  1504063453_1502866628        es        it   
4900  1647862428_1647712939        es        it   
4901  1636570015_1637492652        es        it   

                                                   key1  \
0                        More Trending Stories,Trending   
1     AI,Hardware,Executive Guides,Cloud,Microsoft,S...   
2                                         anaheim-ducks   
3     bengal latest news,mamata banrjee,republicday,...   
4     Broad Street Birmingham,ThingsToDoInBirmingham...   
...                                                 ...   
4897                                         Denver,NBA   
4898                                           EUROSTAT   
4899           vigilancia epidemiológica,ticker,puertos   
4900  ESTADOS UNIDOS,ESTADOSUNIDOS,DONALDTRUMP,IRÁN,...   
4901                                                NaN   

                                                   key2  \
0                        More Trending Stories,Trending   
1     Best Western,Information Security,Privacy,aws,...   
2     keep the hope machine running,new year's resol...   
3     tableaux,WestBengal,Mamata Banerjee,West Benga...   
4     Marvel Cinematic Universe,People's Struggles,a...   
...                                                 ...   
4897  DenverNuggets,coronavirus,Denver Nuggets,Coron...   
4898                                             Estero   
4899                                           serpenti   
4900  corpodelleguardie,magistratura,iran,qasemsolei...   
4901                       JoeBiden,DonaldTrump,NewYork   

                                        key1_translated  \
0                        More Trending Stories,Trending   
1     AI,Hardware,Executive Guides,Cloud,Microsoft,S...   
2                                         anaheim-ducks   
3     bengal latest news,mamata banrjee,republicday,...   
4     Broad Street Birmingham,ThingsToDoInBirmingham...   
...                                                 ...   
4897                                       Denver.,NBA.   
4898                                           Eurostat   
4899         epidemiological surveillance,ticker.,ports   
4900  UNITED STATES,UNITED STATES,Donald Trump.,IRAN...   
4901                                                NaN   

                                        key2_translated     score  
0                        More Trending Stories,Trending  1.000000  
1     Best Western,Information Security,Privacy,aws,...  0.083333  
2     keep the hope machine running,new year's resol...  0.000000  
3     tableaux,WestBengal,Mamata Banerjee,West Benga...  0.000000  
4     Marvel Cinematic Universe,People's Struggles,a...  0.000000  
...                                                 ...       ...  
4897  Denver Nuggets,coronavirus,Denver Nuggets,Coro...  0.000000  
4898                                             Abroad  0.000000  
4899                                             snakes  0.000000  
4900  Corpodelleguardie,judiciary,Iran,Qassem Soleim...  0.666667  
4901                                                NaN -1.000000  

[4902 rows x 8 columns]

In [25]:
path = 'eval/_EVAL_keywords_score.csv'
keywords_score_df.to_csv(path,index=False)
